In [ ]:
#import libraries
import pandas as pd
import numpy as np
import math
import plotly.express as px

Filtering data:

In [ ]:
#getting data
cars_df = pd.read_csv('data/car_prices.csv')
#unifying the brand names
cars_df['make'] = cars_df['make'].str.lower()
toyota_df = cars_df[(cars_df['make'] == 'toyota') | (cars_df['make'] == 'lexus') | (cars_df['make'] == 'scion')].reset_index(drop=True)
toyota_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 53633 entries, 0 to 53632
Data columns (total 16 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   year          53633 non-null  int64  
 1   make          53633 non-null  object 
 2   model         53633 non-null  object 
 3   trim          53627 non-null  object 
 4   body          53419 non-null  object 
 5   transmission  48426 non-null  object 
 6   vin           53633 non-null  object 
 7   state         53633 non-null  object 
 8   condition     52506 non-null  float64
 9   odometer      53625 non-null  float64
 10  color         53614 non-null  object 
 11  interior      53614 non-null  object 
 12  seller        53633 non-null  object 
 13  mmr           53633 non-null  float64
 14  sellingprice  53633 non-null  float64
 15  saledate      53633 non-null  object 
dtypes: float64(4), int64(1), object(11)
memory usage: 6.5+ MB


Filling the missing values:

In [47]:
toyota_df.isna().sum()

year               0
make               0
model              0
trim               6
body             214
transmission    5207
vin                0
state              0
condition       1127
odometer           8
color             19
interior          19
seller             0
mmr                0
sellingprice       0
saledate           0
dtype: int64

In [ ]:
#setting the dictionary for mapping
bodies_dict = {
    'gx' : 'suv',
    'tundra' : 'truck',
    'sienna' : 'minivan',
    'lx' : 'suv',
    'corolla' : 'sedan',
    'matrix' : 'minivan',
    'camry' : 'sedan',
    'yaris' : 'hatchback',
    'previa' : 'minivan',
    'pickup' : 'truck',
    'avalon' : 'sedan'}

#filling the blanks in dataset
toyota_df.loc[toyota_df['body'].isnull(), 'body'] = toyota_df['model'].map(bodies_dict)

In [ ]:
def get_fillna(col):
    return_dict = {}
    #filtering dataset for specific column and getting most common value
    for now in toyota_df[toyota_df[col].isnull()]['model'].value_counts().index:
        mask = toyota_df['model'] == now
        return_dict[now] = toyota_df[mask][col].value_counts().index[0]
    return return_dict

#filling the blanks in dataset
toyota_df.loc[toyota_df['trim'].isnull(), 'trim'] = toyota_df['model'].map(get_fillna('trim'))
toyota_df.loc[toyota_df['transmission'].isnull(), 'transmission'] = toyota_df['model'].map(get_fillna('transmission'))
toyota_df.loc[toyota_df['color'].isnull(), 'color'] = toyota_df['model'].map(get_fillna('color'))
toyota_df.loc[toyota_df['interior'].isnull(), 'interior'] = toyota_df['model'].map(get_fillna('interior'))

In [ ]:
#unifying the model names
toyota_df['model'] = toyota_df['model'].apply(lambda x: str.lower(x))
toyota_df['model']

0         rx 350
1         gs 350
2         es 350
3         rx 350
4        rx 450h
          ...   
53628     matrix
53629    4runner
53630     tundra
53631     tundra
53632     rx 350
Name: model, Length: 53633, dtype: object

In [ ]:
def get_con(row):
    #setting filter from data passed into function
    mask = (toyota_df['model'] == row['model']) & (toyota_df['year'] == row['year'])& (toyota_df['trim'] == row['trim'])
    price_to_find = row['sellingprice']
    #getting value. It's average for records with same model, trim and year
    con = toyota_df[mask].iloc[(toyota_df[mask]['sellingprice'] - price_to_find).abs().argsort()[:2]]['condition'].mean()  
    #checking if value is valid
    if math.isnan(con):
        #simplifying the filter
        mask = (toyota_df['model'] == row['model']) & (toyota_df['trim'] == row['trim'])
        price_to_find = row['year']
        con = toyota_df[mask].iloc[(toyota_df[mask]['sellingprice'] - price_to_find).abs().argsort()[:2]]['condition'].mean()  
    #checking if value is valid
    if math.isnan(con):
        #simplifying the filter
        mask = (toyota_df['model'] == row['model'])
        price_to_find = row['sellingprice']
        con = toyota_df[mask].iloc[(toyota_df[mask]['sellingprice'] - price_to_find).abs().argsort()[:2]]['condition'].mean()  
    #checking if value is valid
    if math.isnan(con):
        #simplifying the filter
        mask = (toyota_df['model'] == row['model']) & (toyota_df['year'] == row['year'])& (toyota_df['trim'] == row['trim'])
        con = toyota_df[mask]['condition'].mean()
    return con

toyota_df.loc[toyota_df['condition'].isna(), 'condition'] = toyota_df[toyota_df['condition'].isna()].apply(get_con, axis=1)

In [ ]:
def get_odo(row):
    #setting filter from data passed into function
    mask = (toyota_df['model'] == row['model']) & (toyota_df['year'] == row['year'])& (toyota_df['trim'] == row['trim'])
    price_to_find = row['sellingprice']
    #getting value. It's average for records with same model, trim and year
    odo = toyota_df[mask].iloc[(toyota_df[mask]['sellingprice'] - price_to_find).abs().argsort()[:2]]['odometer'].mean()  
    #checking if value is valid
    if math.isnan(odo):
        #simplifying the filter
        mask = (toyota_df['model'] == row['model']) & (toyota_df['trim'] == row['trim'])
        price_to_find = row['year']
        odo = toyota_df[mask].iloc[(toyota_df[mask]['sellingprice'] - price_to_find).abs().argsort()[:2]]['odometer'].mean()  
    #checking if value is valid
    if math.isnan(odo):
        #simplifying the filter
        mask = (toyota_df['model'] == row['model'])
        price_to_find = row['sellingprice']
        odo = toyota_df[mask].iloc[(toyota_df[mask]['sellingprice'] - price_to_find).abs().argsort()[:2]]['odometer'].mean()  
    #checking if value is valid
    if math.isnan(odo):
        #simplifying the filter
        mask = (toyota_df['model'] == row['model']) & (toyota_df['year'] == row['year'])& (toyota_df['trim'] == row['trim'])
        odo = toyota_df[mask]['odometer'].mean()
    return odo

toyota_df.loc[toyota_df['odometer'].isna(), 'odometer'] = toyota_df[toyota_df['odometer'].isna()].apply(get_con, axis=1)

In [ ]:
#checking for dulicates
toyota_df.duplicated().value_counts()

False    53633
Name: count, dtype: int64

Outliers processing:

In [ ]:
#buildiing the boxplot to visually find the anomalies
fig = px.box(toyota_df[['sellingprice', 'odometer']], orientation='h')
fig.show()

In [ ]:
#clearing outliers using interquartile range method
for now in ['sellingprice', 'odometer']:
    x=toyota_df[now]
    q1, q2 = x.quantile(0.25), x.quantile(0.75)
    iqr = q2 - q1
    lower = q1 - (1.5*iqr)
    upper = q2 + (1.5 * iqr)
    toyota_df = toyota_df[(x>lower)&(x<upper)]
fig = px.box(toyota_df[['sellingprice', 'odometer']], orientation='h')
fig.show()


In [ ]:
#importing data
toyota_df.to_csv('data/toyota_sales.csv')